In [1]:
import psycopg2

import pandas as pd
import numpy as np

from copy import deepcopy

import ast

import networkx as nx

import matplotlib.pyplot as plt

In [2]:
sehir_matches_by_guid = pd.read_csv('datasets/sehir_matches.csv', index_col="GUID.1").drop("GUID", axis=1)
sehir_matches_by_guid.head(5)

sehir_matches  \
GUID.1                                                          
294557248   [('mustafa demir', 100), ('mustafa gokdemir', ...   
3410655087                             [('melisa yalin', 83)]   
2996348915     [('mustafa durdu', 81), ('mustafa duman', 81)]   
89203798                             [('ahmet karanfil', 81)]   
239841117                                [('derya genc', 82)]   

           twitter_screen_name    twitter_name  \
GUID.1                                           
294557248         mustafedemir   Mustafa DEMİR   
3410655087     selambenmelissa  Melissa Yanıcı   
2996348915         dundar_mstf  Mustafa Dündar   
89203798          AhmetMaranki   Ahmet MARANKİ   
239841117         bayan_sukela        Derya E.   

                                          profile_description  \
GUID.1                                                          
294557248   BEDEN EĞİTİMİ ÖĞRETMENİ \nAli Akkanat Anadolu ...   
3410655087         gizlilikten dolayı fotoğraf yayınlamıyorum   
2996348915                                                NaN   
89203798    Prof. Dr. Ahmet Maranki'nin çalışmalarının yay...   
239841117   Büyük adam olmana lüzum yok, sadece adam ol ye...   

            followers_count  friends_count  favourites_count  statuses_count  \
GUID.1                                                                         
294557248                45             53               349             261   
3410655087           115870            514               117             495   
2996348915              869            306              3669             302   
89203798               4762             28                 0               0   
239841117               567             70                 1            2615   

           lang cleaned_twitter_name  
GUID.1                                
294557248    tr        mustafa demir  
3410655087   tr         melissa yanc  
2996348915   tr       mustafa dundar  
89203798     tr        ahmet maranki  
239841117    tr             derya e.

In [3]:
G = nx.Graph()

In [4]:
df_by_twitter_name = sehir_matches_by_guid.set_index("cleaned_twitter_name")
df_by_twitter_name.head()

sehir_matches  \
cleaned_twitter_name                                                      
mustafa demir         [('mustafa demir', 100), ('mustafa gokdemir', ...   
melissa yanc                                     [('melisa yalin', 83)]   
mustafa dundar           [('mustafa durdu', 81), ('mustafa duman', 81)]   
ahmet maranki                                  [('ahmet karanfil', 81)]   
derya e.                                           [('derya genc', 82)]   

                     twitter_screen_name    twitter_name  \
cleaned_twitter_name                                       
mustafa demir               mustafedemir   Mustafa DEMİR   
melissa yanc             selambenmelissa  Melissa Yanıcı   
mustafa dundar               dundar_mstf  Mustafa Dündar   
ahmet maranki               AhmetMaranki   Ahmet MARANKİ   
derya e.                    bayan_sukela        Derya E.   

                                                    profile_description  \
cleaned_twitter_name                                                      
mustafa demir         BEDEN EĞİTİMİ ÖĞRETMENİ \nAli Akkanat Anadolu ...   
melissa yanc                 gizlilikten dolayı fotoğraf yayınlamıyorum   
mustafa dundar                                                      NaN   
ahmet maranki         Prof. Dr. Ahmet Maranki'nin çalışmalarının yay...   
derya e.              Büyük adam olmana lüzum yok, sadece adam ol ye...   

                      followers_count  friends_count  favourites_count  \
cleaned_twitter_name                                                     
mustafa demir                      45             53               349   
melissa yanc                   115870            514               117   
mustafa dundar                    869            306              3669   
ahmet maranki                    4762             28                 0   
derya e.                          567             70                 1   

                      statuses_count lang  
cleaned_twitter_name                       
mustafa demir                    261   tr  
melissa yanc                     495   tr  
mustafa dundar                   302   tr  
ahmet maranki                      0   tr  
derya e.                        2615   tr

In [5]:
len(df_by_twitter_name)

4063

In [6]:
# for twitter_name in df_by_twitter_name.index:
#     G.add_node(twitter_name)

In [7]:
# for std in sehir_matches_by_guid.index:
#     G.add_node(std)

## Connect to sql Database

In [8]:
connection = psycopg2.connect('dbname=twitter_accounts_new host=localhost user=postgres password=1_sehir_1')

twitter_users = pd.read_sql("SELECT * FROM twitter_user", connection)\
.rename(columns={'id': 'GUID', 
                 'name': 'twitter_name',
                 'description': 'profile_description',
                 'screen_name': 'twitter_screen_name'})

user_connections = pd.read_sql("SELECT * FROM twitter_connection", connection).drop('id', axis=1)

In [9]:
for i, row in user_connections.iterrows():
    from_ = row['from_user_id']
    to = row['to_user_id']
    try:
        G.add_edge(sehir_matches_by_guid.loc[from_]["cleaned_twitter_name"],sehir_matches_by_guid.loc[to]["cleaned_twitter_name"])
    except (KeyError,TypeError) as e:
        continue

In [10]:
G.number_of_nodes()

3677

In [11]:
G.number_of_edges()

5109

## Drawing the Network

In [ ]:
plt.figure(figsize=(100, 100))
graph_no_labels = nx.draw(G, pos=nx.spring_layout(G),with_labels=False)
plt.savefig('no_label_graph.pdf', format='pdf')

In [ ]:
plt.figure(figsize=(100, 100))
graph_no_labels = nx.draw(G, pos=nx.spring_layout(G),with_labels=True)
plt.savefig('graph.pdf', format='pdf')